<a href="https://colab.research.google.com/github/PhonSobon/Khmer_OCR/blob/main/khmer_OCR.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [5]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import tensorflow as tf
import torch
import skimage
import albumentations
import cv2
from PIL import Image

In [6]:
!pip install -U datasets

In [7]:
from datasets import load_dataset

ds = load_dataset("seanghay/khmer-dictionary-44k", split="train")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [8]:
# prompt: show all data in description

print(ds)
print(ds.features)
print(ds[0])
print(ds[:5])
print(ds.info)
print(ds.description)
print(ds.citation)
print(ds.homepage)
print(ds.license)
print(ds.builder_name)
print(ds.config_name)
print(ds.version)
print(ds.num_rows)
print(ds.num_columns)
print(ds.column_names)
print(ds.shape)
print(ds.dataset_size)
print(ds.size_in_bytes)
print(ds.split)
print(ds.data)


Dataset({
    features: ['word', 'pos', 'pro', 'definition', 'example'],
    num_rows: 44706
})
{'word': Value(dtype='string', id=None), 'pos': Value(dtype='string', id=None), 'pro': Value(dtype='string', id=None), 'definition': Value(dtype='string', id=None), 'example': Value(dtype='string', id=None)}
{'word': 'ក', 'pos': 'ន.', 'pro': '[ក]', 'definition': 'តួអក្សរទី១ក្នុងវគ្គទី១នៃអក្ខរក្រមព្យញ្ជនៈខ្មែរ។\xa0តួអក្សរនេះមានឈ្មោះថា\xa0ក\xa0ហើយតាងឱ្យព្យញ្ជនៈ /ក/\xa0មានអក្ខរសូរអន្តរជាតិ\xa0[k]\xa0ជាកណ្ឋជៈ មានសំឡេងក្នុងឋានបំពង់ក ជាសិថិល អឃោសៈ។', 'example': ''}
{'word': ['ក', 'ក', 'ក', 'ក៏', 'កក'], 'pos': ['ន.', 'កិ.', 'ន.', 'ឈ.', 'គុ.កិ., គុ.'], 'pro': ['[ក]', '[ក]', '[ក]', '[ក]', '[កក]'], 'definition': ['តួអក្សរទី១ក្នុងវគ្គទី១នៃអក្ខរក្រមព្យញ្ជនៈខ្មែរ។\xa0តួអក្សរនេះមានឈ្មោះថា\xa0ក\xa0ហើយតាងឱ្យព្យញ្ជនៈ /ក/\xa0មានអក្ខរសូរអន្តរជាតិ\xa0[k]\xa0ជាកណ្ឋជៈ មានសំឡេងក្នុងឋានបំពង់ក ជាសិថិល អឃោសៈ។', 'តាំងផ្ដើម, តាំងធ្វើ', 'អវយវៈដែលតពីក្បាលទៅស្មា ឬទៅខ្លួននៃមនុស្សសត្វ', 'ពាក្យជាសន្ធានមានសំឡេងកញ្ឆក់ខ្លីសម្រា

In [9]:
khmer_hanumans = load_dataset("seanghay/khmer-hanuman-100k")

In [10]:
khmer_hanumans

DatasetDict({
    train: Dataset({
        features: ['image', 'text'],
        num_rows: 100001
    })
})

In [11]:
print(khmer_hanumans['train']['text'])

['Amazon បង្កើនការវិនិយោគជិត១', '០០លានដុល្លារ ទៅក្នុងសេវាកម្មបង់ប្រាក់រ', 'បស់ខ្លួនប្រចាំនៅប្រទេសឥណ្ឌា(ញូដេលី) ៖ក្រុមហ៊ុន', 'លក់ទំនិញអនឡាញដ៏ធំរបស់សហរដ្ឋអាមេរិក Amazon ទើបតែបានបោះទុនចំនួន ៧ពាន់លានរូ', 'ពីថែមទៀត ដែលស្មើនឹង ៩៥.៥១លានដុល្លារ ទៅក្នុ', 'ងសេវាកម្មបង់ប្រាក់របស់ខ្លួនគឺ Amazon Pay ប្រចាំនៅប្រទេសឥណ្ឌា ។នេះបើតាមកា', 'រចេញផ្សាយ ដោយទីភ្នាក់ងារព័ត៌មាន Reuter', 's នៅថ្ងៃសុក្រ ទី០៩ ខែតុលា ឆ្នាំ២', '០២០ ។ការបន្ថែមទុនវិនិយោគនេះធ្វើឡើង ស្របពេលដែលរដូវបុ', 'ណ្យទានសាសនាហិណ្ឌូហៅថា Dussehra និង Diwali កំពុងខិតជិតមកដល់នៅក្នុងប្រទេសឥណ្ឌា ។Amazon នឹងចាប់ផ្តើ', 'មព្រឹត្តិការណ៍លក់', 'បញ្ចុះតម្លៃសម្រាប់ឱកាសបុណ្យទាំងនេះ ចាប់ពីថ្ងៃសៅរ៍សប្តាហ៍ក្រោយតទៅ ខណៈ', 'ក្រុមហ៊ុនលក់ទំនិញអនឡាញលំដាប់ពិភពលោកមួយនេះ បាននិងកំពុងបន្តព្យាយា', 'មជំរុញឱ្យអតិថិជននាំ', 'គ្នាបង់ប្រាក់តាមសេវាកម្ម Amazon', 'Pay របស់ខ្លួន ជាពិសេសនៅប្រទេសឥណ្ឌាតែម្តង ដែលមា', 'នទំហំទីផ្សារយ៉ាងធំសម្បើមមួយ ។គួរជម្រាបថា បច្ចុប្បន្នទីផ្សារលក់', 'ទំនិញអនឡាញនៅឥណ្ឌា ដែលកំពុងរីកធំធាត់យ៉ាងឆាប់រហ័ស', 'ស្ថិតក្រោមការប្រកួតប្រជែងគ្នារវាងក្រុមហ៊ុនធំៗចំនួន៣ គឺក្រុម

In [12]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [13]:
data_label = pd.read_json('/content/drive/MyDrive/Dataset/project-1-at-2025-07-04-09-43-4757d125.json')

In [14]:
data_label

id                                        annotations  \
0   1  [{'id': 1, 'completed_by': 1, 'result': [{'ori...   
1   6  [{'id': 2, 'completed_by': 1, 'result': [{'ori...   

                                     file_upload  \
0                             8f517fad-mptc1.jpg   
1  eacf706e-Consonnes_de_lalphabet_khmer.pdf.jpg   

                                              drafts predictions  \
0  [{'id': 4, 'user': 'phon.sobon02@gmail.com', '...          []   
1                                                 []          []   

                                                data meta  \
0       {'ocr': '/data/upload/1/8f517fad-mptc1.jpg'}   {}   
1  {'ocr': '/data/upload/1/eacf706e-Consonnes_de_...   {}   

                        created_at                       updated_at  inner_id  \
0 2025-06-24 04:29:02.590839+00:00 2025-06-25 07:51:20.056296+00:00         1   
1 2025-06-27 03:02:05.137905+00:00 2025-06-30 01:56:25.079674+00:00         6   

   total_annotations  cancelled_annotations  total_predictions  comment_count  \
0                  1                      0                  0              0   
1                  1                      0                  0              0   

   unresolved_comment_count last_comment_updated_at  project  updated_by  \
0                         0                     NaT        1           1   
1                         0                     NaT        1           1   

  comment_authors  
0              []  
1              []

In [15]:
data_label.columns

Index(['id', 'annotations', 'file_upload', 'drafts', 'predictions', 'data',
       'meta', 'created_at', 'updated_at', 'inner_id', 'total_annotations',
       'cancelled_annotations', 'total_predictions', 'comment_count',
       'unresolved_comment_count', 'last_comment_updated_at', 'project',
       'updated_by', 'comment_authors'],
      dtype='object')

In [16]:
print(data_label['annotations'].iloc[0] )

[{'id': 1, 'completed_by': 1, 'result': [{'original_width': 905, 'original_height': 1280, 'image_rotation': 0, 'value': {'x': 5.942708575142763, 'y': 17.366946778711487, 'width': 8.715972576876055, 'height': 1.6806722689075642, 'rotation': 0}, 'id': 'sgvWoBxNyX', 'from_name': 'bbox', 'to_name': 'image', 'type': 'rectangle', 'origin': 'manual'}, {'original_width': 905, 'original_height': 1280, 'image_rotation': 0, 'value': {'x': 5.942708575142763, 'y': 17.366946778711487, 'width': 8.715972576876055, 'height': 1.6806722689075642, 'rotation': 0, 'labels': ['Title']}, 'id': 'sgvWoBxNyX', 'from_name': 'label', 'to_name': 'image', 'type': 'labels', 'origin': 'manual'}, {'original_width': 905, 'original_height': 1280, 'image_rotation': 0, 'value': {'x': 5.942708575142763, 'y': 17.366946778711487, 'width': 8.715972576876055, 'height': 1.6806722689075642, 'rotation': 0, 'text': ['ក្រសួង']}, 'id': 'sgvWoBxNyX', 'from_name': 'transcription', 'to_name': 'image', 'type': 'textarea', 'origin': 'manu

In [17]:
import pandas as pd
import json
from PIL import Image, ImageDraw, ImageFont
import matplotlib.pyplot as plt
import os
from google.colab import drive
import requests

drive.mount('/content/drive')

font_url = "https://github.com/googlefonts/noto-fonts/raw/main/hinted/ttf/NotoSansKhmer/NotoSansKhmer-Regular.ttf"
font_path = "/content/KhmerFont.ttf"
!wget {font_url} -O {font_path}

json_path = '/content/drive/MyDrive/Dataset/project-1-at-2025-07-04-09-43-4757d125.json'
with open(json_path, 'r', encoding='utf-8') as f:
    data = json.load(f)

# Create output directory
output_dir = '/content/drive/MyDrive/Dataset/label/Khmer_Text_Images'
os.makedirs(output_dir, exist_ok=True)

# Initialize results list
results = []

# Function to create text image
def create_text_image(text, output_path, width=400, height=150, font_size=40):
    img = Image.new('RGB', (width, height), color='white')
    draw = ImageDraw.Draw(img)

    try:
        font = ImageFont.truetype(font_path, font_size)
    except:
        raise Exception("Failed to load Khmer font")

    # Calculate text position (centered)
    bbox = draw.textbbox((0, 0), text, font=font)
    text_width = bbox[2] - bbox[0]
    text_height = bbox[3] - bbox[1]
    x = (width - text_width) // 2
    y = (height - text_height) // 2

    draw.text((x, y), text, fill='black', font=font)
    img.save(output_path)

# Process all text annotations
image_counter = 1
for item in data[0]['annotations'][0]['result']:
    if item['type'] == 'textarea':
        text = item['value']['text'][0]
        output_filename = f"image{image_counter:02d}.jpg"
        output_path = os.path.join(output_dir, output_filename)

        try:
            create_text_image(text, output_path)
            results.append({
                'image_file': output_filename,
                'khmer_text': text,
            })
            print(f"Created {output_filename} with text: {text}")
            image_counter += 1
        except Exception as e:
            results.append({
                'image_file': output_filename,
                'khmer_text': text,
                'status': f"Failed: {str(e)}"
            })

# Save results to txt
results_df = pd.DataFrame(results)
results_csv_path = os.path.join(output_dir, '/content/drive/MyDrive/Dataset/label/text_images_index.txt')
results_df.to_csv(results_csv_path, index=False, encoding='utf-8-sig')

print("\nProcessing complete!")
print(f"Total images created: {len(results_df)}")
print(f"Saved to: {output_dir}")
print("\nFirst 5 results:")
print(results_df.head())
plt.tight_layout()
plt.show()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
--2025-07-04 09:13:08--  https://github.com/googlefonts/noto-fonts/raw/main/hinted/ttf/NotoSansKhmer/NotoSansKhmer-Regular.ttf
Resolving github.com (github.com)... 140.82.114.4
Connecting to github.com (github.com)|140.82.114.4|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://github.com/notofonts/noto-fonts/raw/main/hinted/ttf/NotoSansKhmer/NotoSansKhmer-Regular.ttf [following]
--2025-07-04 09:13:08--  https://github.com/notofonts/noto-fonts/raw/main/hinted/ttf/NotoSansKhmer/NotoSansKhmer-Regular.ttf
Reusing existing connection to github.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/notofonts/noto-fonts/main/hinted/ttf/NotoSansKhmer/NotoSansKhmer-Regular.ttf [following]
--2025-07-04 09:13:08--  https://raw.githubusercontent.com/notofonts/noto-fonts/main/

<Figure size 640x480 with 0 Axes>